In [5]:
import toml

raw_data = toml.load('cube_81183_tag_data.toml')
raw_data

{'Abhorrent Overlord': {'mana_cost': ['5', 'B', 'B'],
  'color_identity': 'B',
  'types': ['creature'],
  'tags': ['Reanimator - Payoff', 'Big', 'Keyword', 'ETB - Enabler']},
 'Abzan Battle Priest': {'mana_cost': ['3', 'W'],
  'color_identity': 'W',
  'types': ['creature'],
  'tags': ['Counters - Enabler',
   'Counters - Payoff',
   'Keyword',
   'Lifegain - Enabler']},
 'Accorder Paladin': {'mana_cost': ['1', 'W'],
  'color_identity': 'W',
  'types': ['creature'],
  'tags': ['Tokens - Payoff', 'Keyword']},
 'Adarkar Wastes': {'mana_cost': [],
  'color_identity': 'C',
  'types': ['land'],
  'tags': []},
 'Adeliz, the Cinder Wind': {'mana_cost': ['1', 'U', 'R'],
  'color_identity': 'UR',
  'types': ['creature'],
  'tags': ['Spells - Payoff', 'Wizards - Payoff', 'Wizards - Enabler']},
 "Ajani's Pridemate": {'mana_cost': ['1', 'W'],
  'color_identity': 'W',
  'types': ['creature'],
  'tags': ['Lifegain - Payoff']},
 'Akroan Crusader': {'mana_cost': ['R'],
  'color_identity': 'R',
  'types

In [6]:
def parse_syn_tags(tags):
    syn_tags = {}
    for tag in tags:
        if '-' in tag:
            k, v = tag.split('-')
            syn_tags.setdefault(k.strip(), []).append(v.strip())

    return syn_tags

In [7]:
cards = {k: parse_syn_tags(v['tags']) for k, v in raw_data.items()}

In [8]:
cards['Abzan Battle Priest']

{'Counters': ['Enabler', 'Payoff'], 'Lifegain': ['Enabler']}

In [9]:
bp_graphs = {}

# e.g. 'Anax and Cymede', {'Heroic': 'Payoff'}
for name, tags in cards.items():
    # e.g. 'Heroic', 'Payoff'
    for theme, roles in tags.items():
        for role in roles:
            bp_graphs.setdefault(theme, {})
            bp_graphs[theme].setdefault(role, set()).add(name)

bp_graphs

{'Reanimator': {'Payoff': {'Abhorrent Overlord',
   'Magmatic Force',
   'Omnath, Locus of Rage',
   'Scourge of Nel Toth'},
  'Enabler': {'Stitch Together',
   'Victimize',
   'Whisper, Blood Liturgist',
   'Zombify'}},
 'ETB': {'Enabler': {'Abhorrent Overlord',
   'Anafenza, Kin-Tree Spirit',
   'Armorcraft Judge',
   'Augury Owl',
   'Banisher Priest',
   'Bloodline Necromancer',
   'Brain Maggot',
   'Cloudblazer',
   'Crested Herdcaller',
   'Daring Archaeologist',
   'Deadeye Harpooner',
   'Dinrova Horror',
   'Dusk Legion Zealot',
   'Enthralling Victor',
   'Gallant Cavalry',
   'Generous Patron',
   'Glint-Nest Crane',
   'Goblin Instigator',
   'Gonti, Lord of Luxury',
   'Greenwarden of Murasa',
   'Harbinger of the Tides',
   'Haunted Dead',
   'Inspiring Cleric',
   'Juniper Order Ranger',
   'Kiri-Onna',
   "Liliana's Specter",
   'Maverick Thopterist',
   'Militia Bugler',
   'Naru Meha, Master Wizard',
   'Possessed Skaab',
   'Ravenous Rats',
   'Rishkar, Peema Renega

In [15]:
import networkx as nx

G = nx.Graph()
for name in cards:
    G.add_node(name)

len(G.nodes)

373

In [17]:
for theme, roles in bp_graphs.items():
    partitions = list(roles.values())
    if len(partitions) != 2:
        # Enabler/Payoff is only tagging scheme supported currently'
        continue
    for card_1 in partitions[0]:
        for card_2 in partitions[1]:
            if card_1 != card_2:
                G.add_edge(card_1, card_2)

len(G.edges)

3906

In [21]:
gainlands = ['Bloodfell Caves', 'Blossoming Sands', 'Dismal Backwater', 'Jungle Hollow', 'Rugged Highlands',
'Scoured Barrens', 'Swiftwater Cliffs', 'Thornwood Falls', 'Tranquil Cove', 'Wind-Scarred Crag']

G.remove_nodes_from(gainlands)
len(G.nodes)

363

In [22]:
C = list(G.subgraph(c) for c in nx.connected_components(G))[0]

len(C.nodes)

303

In [23]:
ecc = nx.eccentricity(C)

In [24]:
ecc_buckets = {}
for k, v in ecc.items():
    ecc_buckets.setdefault(v, []).append(k)
ecc_buckets

{4: ['Abhorrent Overlord',
  'Accorder Paladin',
  "Ajani's Pridemate",
  'Akroan Crusader',
  'Anafenza, Kin-Tree Spirit',
  'Anax and Cymede',
  'Angel of Flight Alabaster',
  'Anowon, the Ruin Sage',
  'Arcbond',
  'Arena Athlete',
  'Armorcraft Judge',
  'Augury Owl',
  'Ayli, Eternal Pilgrim',
  'Azami, Lady of Scrolls',
  'Azorius Signet',
  'Azra Oddsmaker',
  'Banisher Priest',
  'Bedlam Reveler',
  'Bishop of Rebirth',
  'Blade of the Bloodchief',
  'Blood Artist',
  'Bloodline Necromancer',
  'Bloodrage Brawler',
  'Bloodsoaked Champion',
  'Bloodspore Thrinax',
  'Bomat Courier',
  'Bone Picker',
  'Bone Splinters',
  'Boros Signet',
  'Brago, King Eternal',
  'Brain Maggot',
  'Brimstone Volley',
  'Brittle Effigy',
  'Cathartic Reunion',
  'Chart a Course',
  'Cloudblazer',
  'Cloudfin Raptor',
  'Collateral Damage',
  'Commune with the Gods',
  'Countryside Crusher',
  'Crawling Sensation',
  'Crested Sunmare',
  'Crovax the Cursed',
  'Crusader of Odric',
  'Crush of Ten

In [25]:
{k: len(v) for k, v in ecc_buckets.items()}

{4: 223, 3: 52, 5: 28}

In [26]:
ecc_buckets[3]

['Abzan Battle Priest',
 'Adeliz, the Cinder Wind',
 'Asylum Visitor',
 'Bloodhall Priest',
 'Buried Ruin',
 'Call to the Feast',
 'Crested Herdcaller',
 'Daring Archaeologist',
 'Drake Haven',
 'Fiery Temper',
 'Fists of Ironwood',
 'Flameblade Adept',
 'Foundry of the Consuls',
 'Gallant Cavalry',
 'Gather the Townsfolk',
 'Glint-Nest Crane',
 'Goblin Assault',
 'Goblin Instigator',
 'Haunted Dead',
 'Izzet Chemister',
 'Juniper Order Ranger',
 'Kari Zev, Skyship Raider',
 'Kindly Stranger',
 'Launch the Fleet',
 'Magus of the Scroll',
 'Maverick Thopterist',
 'Mavren Fein, Dusk Apostle',
 'Mercy Killing',
 'Mindless Automaton',
 'Mindstorm Crown',
 'Naru Meha, Master Wizard',
 'Nearheath Chaplain',
 'Path of Discovery',
 'Presence of Gond',
 'Rise from the Tides',
 'Runehorn Hellkite',
 'Saproling Migration',
 'Scourge Wolf',
 'Selesnya Evangel',
 'Skilled Animator',
 'Skullmulcher',
 'Soulfire Grand Master',
 'Spore Swarm',
 'Steward of Solidarity',
 'The Flame of Keld',
 'Thopter 

In [27]:
nx.single_source_shortest_path(C, 'Abzan Battle Priest')

{'Abzan Battle Priest': ['Abzan Battle Priest'],
 'Ordeal of Thassa': ['Abzan Battle Priest', 'Ordeal of Thassa'],
 'Gird for Battle': ['Abzan Battle Priest', 'Gird for Battle'],
 'Crovax the Cursed': ['Abzan Battle Priest', 'Crovax the Cursed'],
 'Skullmulcher': ['Abzan Battle Priest', 'Skullmulcher'],
 'Blade of the Bloodchief': ['Abzan Battle Priest', 'Blade of the Bloodchief'],
 'Mindless Automaton': ['Abzan Battle Priest', 'Mindless Automaton'],
 'Reap What Is Sown': ['Abzan Battle Priest', 'Reap What Is Sown'],
 'Scrounging Bandar': ['Abzan Battle Priest', 'Scrounging Bandar'],
 'Phalanx Leader': ['Abzan Battle Priest', 'Phalanx Leader'],
 'Indulgent Aristocrat': ['Abzan Battle Priest', 'Indulgent Aristocrat'],
 'Juniper Order Ranger': ['Abzan Battle Priest', 'Juniper Order Ranger'],
 'Gyre Sage': ['Abzan Battle Priest', 'Gyre Sage'],
 'Thopter Squadron': ['Abzan Battle Priest', 'Thopter Squadron'],
 'Renegade Krasis': ['Abzan Battle Priest', 'Renegade Krasis'],
 'Armorcraft Judg

In [51]:
sps = list(nx.all_simple_paths(C, 'Abzan Battle Priest', 'Rise from the Tides', cutoff=3))

In [53]:
sps

[['Abzan Battle Priest',
  'Ordeal of Thassa',
  'Gird for Battle',
  'Rise from the Tides'],
 ['Abzan Battle Priest',
  'Ordeal of Thassa',
  'Path of Discovery',
  'Rise from the Tides'],
 ['Abzan Battle Priest',
  'Gird for Battle',
  "Pyromancer's Goggles",
  'Rise from the Tides'],
 ['Abzan Battle Priest',
  'Gird for Battle',
  'Cryptic Serpent',
  'Rise from the Tides'],
 ['Abzan Battle Priest',
  'Gird for Battle',
  'Adeliz, the Cinder Wind',
  'Rise from the Tides'],
 ['Abzan Battle Priest',
  'Gird for Battle',
  'Jhessian Thief',
  'Rise from the Tides'],
 ['Abzan Battle Priest',
  'Gird for Battle',
  'Thing in the Ice',
  'Rise from the Tides'],
 ['Abzan Battle Priest',
  'Gird for Battle',
  'Izzet Chemister',
  'Rise from the Tides'],
 ['Abzan Battle Priest',
  'Gird for Battle',
  'Soulfire Grand Master',
  'Rise from the Tides'],
 ['Abzan Battle Priest',
  'Gird for Battle',
  'Bedlam Reveler',
  'Rise from the Tides'],
 ['Abzan Battle Priest',
  'Gird for Battle',
  

In [34]:
list(nx.all_shortest_paths(C, 'Abzan Battle Priest', 'Kalastria Highborn'))

[['Abzan Battle Priest', 'Crovax the Cursed', 'Kalastria Highborn'],
 ['Abzan Battle Priest', 'Blade of the Bloodchief', 'Kalastria Highborn'],
 ['Abzan Battle Priest', 'Indulgent Aristocrat', 'Kalastria Highborn'],
 ['Abzan Battle Priest', 'Oathsworn Vampire', 'Kalastria Highborn'],
 ['Abzan Battle Priest', 'Path of Bravery', 'Kalastria Highborn'],
 ['Abzan Battle Priest', 'Ayli, Eternal Pilgrim', 'Kalastria Highborn'],
 ['Abzan Battle Priest', 'Felidar Sovereign', 'Kalastria Highborn'],
 ['Abzan Battle Priest', "Ajani's Pridemate", 'Kalastria Highborn'],
 ['Abzan Battle Priest', 'Crested Sunmare', 'Kalastria Highborn'],
 ['Abzan Battle Priest', 'Vizkopa Guildmage', 'Kalastria Highborn'],
 ['Abzan Battle Priest', 'Lone Rider', 'Kalastria Highborn']]

In [33]:
list(nx.all_shortest_paths(C, 'Abzan Battle Priest', 'Rise from the Tides'))

[['Abzan Battle Priest', 'Gird for Battle', 'Rise from the Tides'],
 ['Abzan Battle Priest', 'Path of Discovery', 'Rise from the Tides']]

In [55]:
start_node = 'Abzan Battle Priest'
#paths = {k: list(nx.all_shortest_paths(C, start_node, k)) for k in C.nodes}

paths = {k: list(nx.all_simple_paths(C, start_node, k, cutoff=3)) for k in C.nodes}

#for end_node in C.nodes:
#    paths[end_node] = list(nx.all_shortest_paths(C, start_node, end_node))

paths

{'Abhorrent Overlord': [['Abzan Battle Priest',
   'Skullmulcher',
   "Illusionist's Stratagem",
   'Abhorrent Overlord'],
  ['Abzan Battle Priest',
   'Skullmulcher',
   'Crush of Tentacles',
   'Abhorrent Overlord'],
  ['Abzan Battle Priest',
   'Skullmulcher',
   'Peel from Reality',
   'Abhorrent Overlord'],
  ['Abzan Battle Priest',
   'Skullmulcher',
   'Supernatural Stamina',
   'Abhorrent Overlord'],
  ['Abzan Battle Priest',
   'Skullmulcher',
   'Panharmonicon',
   'Abhorrent Overlord'],
  ['Abzan Battle Priest',
   'Skullmulcher',
   'Vizier of Deferment',
   'Abhorrent Overlord'],
  ['Abzan Battle Priest',
   'Skullmulcher',
   'Mirror Mockery',
   'Abhorrent Overlord'],
  ['Abzan Battle Priest',
   'Skullmulcher',
   'Brago, King Eternal',
   'Abhorrent Overlord'],
  ['Abzan Battle Priest',
   'Skullmulcher',
   'Whisper, Blood Liturgist',
   'Abhorrent Overlord'],
  ['Abzan Battle Priest',
   'Juniper Order Ranger',
   "Illusionist's Stratagem",
   'Abhorrent Overlord'],


In [77]:
list(nx.all_simple_paths(C, start_node, 'Reap What Is Sown', cutoff=3))

[['Abzan Battle Priest',
  'Ordeal of Thassa',
  'Thopter Squadron',
  'Reap What Is Sown'],
 ['Abzan Battle Priest',
  'Ordeal of Thassa',
  'Mindless Automaton',
  'Reap What Is Sown'],
 ['Abzan Battle Priest',
  'Ordeal of Thassa',
  'Renegade Krasis',
  'Reap What Is Sown'],
 ['Abzan Battle Priest',
  'Ordeal of Thassa',
  'Armorcraft Judge',
  'Reap What Is Sown'],
 ['Abzan Battle Priest',
  'Ordeal of Thassa',
  'Tuskguard Captain',
  'Reap What Is Sown'],
 ['Abzan Battle Priest',
  'Ordeal of Thassa',
  'Hardened Scales',
  'Reap What Is Sown'],
 ['Abzan Battle Priest',
  'Ordeal of Thassa',
  'Generous Patron',
  'Reap What Is Sown'],
 ['Abzan Battle Priest', 'Ordeal of Thassa', 'Reap What Is Sown'],
 ['Abzan Battle Priest',
  'Gird for Battle',
  'Thopter Squadron',
  'Reap What Is Sown'],
 ['Abzan Battle Priest',
  'Gird for Battle',
  'Mindless Automaton',
  'Reap What Is Sown'],
 ['Abzan Battle Priest',
  'Gird for Battle',
  'Ordeal of Thassa',
  'Reap What Is Sown'],
 ['A

In [65]:
num_paths = []

for k, v in paths.items():
    if len(v) > 0:
        path_length = len(v[0])
        num_paths.append((k, len(v)))

num_paths.sort(key=lambda tup: tup[1], reverse=True)
num_paths

[('Blade of the Bloodchief', 508),
 ('Skullmulcher', 506),
 ('Indulgent Aristocrat', 492),
 ('Thopter Squadron', 490),
 ('Metallic Mimic', 483),
 ('Mindless Automaton', 478),
 ('Juniper Order Ranger', 467),
 ('Bloodspore Thrinax', 460),
 ('Generous Patron', 456),
 ('Path of Bravery', 456),
 ('Path of Discovery', 437),
 ('Armorcraft Judge', 429),
 ('Mikaeus, the Lunarch', 421),
 ('Ordeal of Thassa', 418),
 ('Renegade Krasis', 410),
 ('Tuskguard Captain', 410),
 ('Hardened Scales', 383),
 ('Crovax the Cursed', 382),
 ('Steel Overseer', 348),
 ('Maverick Thopterist', 343),
 ('Launch the Fleet', 338),
 ('Jeskai Ascendancy', 322),
 ('Ordeal of Heliod', 318),
 ('Mavren Fein, Dusk Apostle', 315),
 ('Bloodline Necromancer', 313),
 ('Teysa, Orzhov Scion', 304),
 ('Oathsworn Vampire', 289),
 ('Phalanx Leader', 288),
 ('Anafenza, Kin-Tree Spirit', 285),
 ('Vizkopa Guildmage', 284),
 ('Ayli, Eternal Pilgrim', 282),
 ('Felidar Sovereign', 282),
 ('Lone Rider', 282),
 ('Rishkar, Peema Renegade', 278

In [64]:
num_paths = {}

for k, v in paths.items():
    if len(v) > 0:
        path_length = len(v[0])
        num_paths.setdefault(path_length, []).append((k, len(v)))

num_paths = {k: sorted(v, key=lambda tup: tup[1], reverse=True) for k, v in num_paths.items()}
num_paths

{4: [('Blade of the Bloodchief', 508),
  ('Skullmulcher', 506),
  ('Indulgent Aristocrat', 492),
  ('Metallic Mimic', 483),
  ('Mindless Automaton', 478),
  ('Juniper Order Ranger', 467),
  ('Bloodspore Thrinax', 460),
  ('Generous Patron', 456),
  ('Path of Bravery', 456),
  ('Path of Discovery', 437),
  ('Armorcraft Judge', 429),
  ('Mikaeus, the Lunarch', 421),
  ('Renegade Krasis', 410),
  ('Tuskguard Captain', 410),
  ('Hardened Scales', 383),
  ('Crovax the Cursed', 382),
  ('Steel Overseer', 348),
  ('Maverick Thopterist', 343),
  ('Launch the Fleet', 338),
  ('Jeskai Ascendancy', 322),
  ('Ordeal of Heliod', 318),
  ('Mavren Fein, Dusk Apostle', 315),
  ('Bloodline Necromancer', 313),
  ('Teysa, Orzhov Scion', 304),
  ('Oathsworn Vampire', 289),
  ('Phalanx Leader', 288),
  ('Anafenza, Kin-Tree Spirit', 285),
  ('Vizkopa Guildmage', 284),
  ('Ayli, Eternal Pilgrim', 282),
  ('Felidar Sovereign', 282),
  ('Lone Rider', 282),
  ('Rishkar, Peema Renegade', 278),
  ('Gird for Battl

In [37]:
num_paths[3]

[('Mavren Fein, Dusk Apostle', 17),
 ('Call to the Feast', 16),
 ('Nearheath Chaplain', 14),
 ('Martyr of Dusk', 13),
 ('Bloodline Necromancer', 11),
 ('Kalastria Highborn', 11),
 ('Maverick Thopterist', 11),
 ('Sanctum Seeker', 11),
 ('Blood Artist', 10),
 ('Goblin Assault', 10),
 ('Goblin Instigator', 10),
 ('Inspiring Cleric', 10),
 ('Kari Zev, Skyship Raider', 10),
 ('Vampire Nighthawk', 10),
 ('Filigree Familiar', 9),
 ('Grazing Gladehart', 9),
 ('Soulfire Grand Master', 9),
 ('Swift Justice', 9),
 ('Brion Stoutarm', 8),
 ('Cloudblazer', 8),
 ('Fists of Ironwood', 8),
 ('Foundry of the Consuls', 8),
 ('Launch the Fleet', 8),
 ('Lightning Helix', 8),
 ('Presence of Gond', 8),
 ('Rhox Faithmender', 8),
 ('River Hoopoe', 8),
 ('Vampiric Rites', 8),
 ('Verdant Embrace', 8),
 ('Young Pyromancer', 8),
 ('Crested Herdcaller', 7),
 ('Gallant Cavalry', 7),
 ('Gather the Townsfolk', 7),
 ('Haunted Dead', 7),
 ('Mercy Killing', 7),
 ('Panharmonicon', 7),
 ('Saproling Migration', 7),
 ('Seles

In [41]:
num_paths[4]

[('Vengeful Rebel', 131),
 ('Collateral Damage', 111),
 ('Rowdy Crew', 103),
 ('Satyr Wayfinder', 87),
 ('Cathartic Reunion', 79),
 ('Chart a Course', 79),
 ('Bone Picker', 76),
 ('Bone Splinters', 76),
 ('Dark-Dweller Oracle', 76),
 ('Magmaw', 76),
 ('Tuktuk the Explorer', 76),
 ('Tymaret, the Murder King', 76),
 ('Harbinger of the Tides', 74),
 ('Spawnbroker', 74),
 ('Watertrap Weaver', 74),
 ('Kiri-Onna', 69),
 ('Tower Geist', 69),
 ('Dismissive Pyromancer', 67),
 ('Magus of the Wheel', 67),
 ('Epiphany at the Drownyard', 63),
 ("Fortune's Favor", 63),
 ("Fa'adiyah Seer", 59),
 ('Abhorrent Overlord', 56),
 ('World Shaper', 56),
 ('Augury Owl', 55),
 ('Banisher Priest', 55),
 ('Brain Maggot', 55),
 ('Deadeye Harpooner', 55),
 ('Dinrova Horror', 55),
 ('Gonti, Lord of Luxury', 55),
 ("Liliana's Specter", 55),
 ('Militia Bugler', 55),
 ('Possessed Skaab', 55),
 ('Ravenous Rats', 55),
 ('Sifter Wurm', 55),
 ('Urbis Protector', 55),
 ('Wall of Omens', 55),
 ('Dissolve', 54),
 ('Mana Leak

In [43]:
paths['Abhorrent Overlord']

[['Abzan Battle Priest',
  'Skullmulcher',
  "Illusionist's Stratagem",
  'Abhorrent Overlord'],
 ['Abzan Battle Priest',
  'Juniper Order Ranger',
  "Illusionist's Stratagem",
  'Abhorrent Overlord'],
 ['Abzan Battle Priest',
  'Armorcraft Judge',
  "Illusionist's Stratagem",
  'Abhorrent Overlord'],
 ['Abzan Battle Priest',
  'Generous Patron',
  "Illusionist's Stratagem",
  'Abhorrent Overlord'],
 ['Abzan Battle Priest',
  'Rishkar, Peema Renegade',
  "Illusionist's Stratagem",
  'Abhorrent Overlord'],
 ['Abzan Battle Priest',
  'Anafenza, Kin-Tree Spirit',
  "Illusionist's Stratagem",
  'Abhorrent Overlord'],
 ['Abzan Battle Priest',
  'Skullmulcher',
  'Crush of Tentacles',
  'Abhorrent Overlord'],
 ['Abzan Battle Priest',
  'Juniper Order Ranger',
  'Crush of Tentacles',
  'Abhorrent Overlord'],
 ['Abzan Battle Priest',
  'Armorcraft Judge',
  'Crush of Tentacles',
  'Abhorrent Overlord'],
 ['Abzan Battle Priest',
  'Generous Patron',
  'Crush of Tentacles',
  'Abhorrent Overlord

In [8]:
def castable(color_id, colors):
    return set(color_id).issubset(set(colors)) or color_id == 'C'

In [75]:
def colors_subgraph(graph, colors):
    on_color = [k for k, v in raw_data.items() 
                        if castable(v['color_identity'], colors)
                        if k in graph.nodes]
    return graph.subgraph(on_color)

In [129]:
import urllib

def image_html(name):
    url_prefix = 'https://api.scryfall.com/cards/named?'
    params = urllib.parse.urlencode({'format': 'image', 'exact': name})
    return '<img src="{}{}" width="146" height="204" class="card-image" />'.format(url_prefix, params)

In [104]:
from IPython.core.display import display, HTML

def card_list_html(cards):
    html = ''
    for card in cards:
        html += image_html(card) + '\n'
    return html

In [90]:
def contains_all_colors(community, colors):
    colors_seen = set()
    for cardname in community:
        color_id = raw_data[cardname]['color_identity']
    
        if color_id != 'C':
            for color in color_id:
                colors_seen.add(color)
    
    return colors_seen == set(colors)

In [130]:
from networkx.algorithms import community

output_html = """
<style>
card-image {
    display: inline;
    margin: 1px;
}
</style>
"""

for colors in ['WU', 'WB', 'WR', 'WG', 'UB', 'UR', 'UG', 'BR', 'BG', 'RG']:
    output_html += 'Colors: {} <br>\n'.format(colors)
    subgraph = colors_subgraph(C, colors)
    colors_gmc = community.greedy_modularity_communities(subgraph)

    i = 0
    for gmc in colors_gmc:
        if not contains_all_colors(gmc, colors):
            continue
        
        output_html += 'Community {}\n'.format(i)
        output_html += '<div>\n{}</div>\n'.format(card_list_html(gmc))
        i += 1

print(output_html)



<style>
card-image {
    display: inline;
    margin: 1px;
}
</style>
Colors: WU <br>
Community 0
<div>
<img src="https://api.scryfall.com/cards/named?format=image&exact=Mikaeus%2C+the+Lunarch" width="146" height="204" class="card-image" />
<img src="https://api.scryfall.com/cards/named?format=image&exact=Foundry+Inspector" width="146" height="204" class="card-image" />
<img src="https://api.scryfall.com/cards/named?format=image&exact=Cultivator%27s+Caravan" width="146" height="204" class="card-image" />
<img src="https://api.scryfall.com/cards/named?format=image&exact=Metalwork+Colossus" width="146" height="204" class="card-image" />
<img src="https://api.scryfall.com/cards/named?format=image&exact=Palladium+Myr" width="146" height="204" class="card-image" />
<img src="https://api.scryfall.com/cards/named?format=image&exact=Ordeal+of+Thassa" width="146" height="204" class="card-image" />
<img src="https://api.scryfall.com/cards/named?format=image&exact=Blade+of+the+Bloodchief" width=

In [131]:
with open('colorpairs.html', 'w') as f:
    f.write(output_html)